In [1]:
%matplotlib inline

In [2]:
import math
import os
import re
from collections import OrderedDict, Counter
from functools import partial
from glob import glob
from multiprocessing import Pool, freeze_support
from subprocess import DEVNULL, run
from tempfile import TemporaryDirectory

import numpy as np
import scipy.signal as ss
import wfdb
from sklearn.neighbors import KernelDensity
from tqdm import tqdm, tqdm_notebook
from wfdb import processing

In [3]:
LEADS = ("I", "II", "III", "aVR", "aVL", "aVF",
         "V1", "V2", "V3", "V4", "V5", "V6")
LABELS = ("AF", "I-AVB", "LBBB", "Normal", 
          "PAC", "PVC", "RBBB", "STD", "STE")
ANN_SYMBS = ("(", ")", "p", "N", "t")

record_names = tuple(sorted(
    fn.split(".hea")[0] for fn in glob("Training_WFDB/*.hea")
))

In [14]:
def _ecgpuwave_ann(sig_idx, r=None, temp_dir="", ann_dir=None):
    if ann_dir:
        # maybe this record has been processed already
        try:
            r_pth = os.path.join(ann_dir, r.record_name)
            return sig_idx, wfdb.rdann(r_pth, f"atr{sig_idx}")
        except:
            # nope, fallback to the ecgpuwave code
            pass
    try:
        # Convert the analogue p_signal into a digital d_signal for write
        r.adc(inplace=True)
        r.wrsamp(write_dir=temp_dir)
        # Convert the digital d_signal back into an analogue p_signal
        r.dac(inplace=True)

        r_pth = os.path.join(temp_dir, r.record_name)
        run(
            f"ecgpuwave -r {r.record_name} -a atr{sig_idx} -s {sig_idx}",
            cwd=temp_dir,
            shell=True,
            check=True,
            stdout=DEVNULL,
            stderr=DEVNULL,
        )
        ann = wfdb.rdann(r_pth, f"atr{sig_idx}")
        if len(ann.signal):
            return sig_idx, ann
    except Exception as e:
        pass
    return None, True

def _get_stats(iterable):
    r_max = np.amax(iterable)
    r_min = np.amin(iterable)
    r_median = np.median(iterable)
    r_mean = np.mean(iterable)
    r_var = np.var(iterable)
    r_std = np.std(iterable)
    return np.array(
        [r_max, r_min, r_median, r_mean, r_var, r_std]
    )

def extract_features(record_name, ann_dir=None):
    """Modifies the record `r` in-place while extracting features
    """
    
    r = wfdb.rdrecord(record_name)

    features = OrderedDict()
    if r.p_signal is None:
        r.dac(inplace=True)
    # print(r.p_signal.shape) # sequence length, number of channels
    seq_len, num_signals = r.p_signal.shape

    # Step 0: Get all possible information from the record comments
    for comment in r.comments:
        dx_grp = re.search(r"^Dx: (?P<dx>.*)$", comment)
        if dx_grp:
            target = [0.0] * len(LABELS)
            for dxi in dx_grp.group("dx").split(","):
                target[LABELS.index(dxi)] = 1.0
            features["target"] = np.array(target)
            continue

        age_grp = re.search(r"^Age: (?P<age>.*)$", comment)
        if age_grp:
            age = float(age_grp.group("age"))
            if math.isnan(age):
                age = -1.0
            features["age"] = np.array([age,])
            continue

        sx_grp = re.search(r"^Sex: (?P<sx>.*)$", comment)
        if sx_grp:
            sex = [0.0, 0.0]  # Male, Female
            if sx_grp.group("sx").upper().startswith("M"):
                sex[0] = 1.0
            elif sx_grp.group("sx").upper().startswith("F"):
                sex[1] = 1.0
            else:
                # patient sex was not provided, leave as zeros for both
                pass
            features["sex"] = np.array(sex)
            continue
    
    # Step 1: Filter out frequencies not within cutoff frequencies
    # Finite Impulse Response filter ("FIR")
    order = int(0.3 * r.fs)
    if order % 2 == 0:
        order += 1

    sig_filter = ss.firwin(
        numtaps=order,
        cutoff=[3, 45],
        pass_zero=False,
        fs=r.fs
    )
    r.p_signal = ss.filtfilt(b=sig_filter, a=np.array([1]), x=r.p_signal, axis=0)

    # Step 2: ECGPUWAVE algorithm for P-wave, QRS-complex, T-wave peak and waveform annotation
    with TemporaryDirectory() as temp_dir:
        worker_fn = partial(_ecgpuwave_ann, r=r, temp_dir=temp_dir, ann_dir=ann_dir)
        signals = list(range(num_signals))
        # Try to multiprocess, but fall back to single process method
        try:
            with Pool(len(os.sched_getaffinity(0))) as p:
                signal_anns = dict(p.imap(worker_fn, signals,))
        except Exception:
            signal_anns = dict([worker_fn(signal) for signal in signals])

    # removes the lead signals that could not be annotated
    signal_anns.pop(None, False)
    ecgpuwave_pass = np.zeros(len(LEADS))

    for sig_idx, ann in signal_anns.items():
        ecgpuwave_pass[sig_idx] = 1
        if ann_dir is not None:
            # fails because wfdb lib enforces only A-Za-z ext :(
            ann.wrann(write_dir=ann_dir)
            # force modify the wfdb library to ignore this warning
            
    features["ecgpuwave_pass"] = ecgpuwave_pass

    # if a lead could not be annotated, use the 'best' quality lead as the fallback lead
    # compare each annotation with each other, pick the one with the highest true positive count
    sig_ann_keys = list(signal_anns.keys())
    sig_ann_tp_count = dict([(k,0) for k in sig_ann_keys])

    for idx_0, key_0 in enumerate(sig_ann_keys):
        ann_0 = signal_anns[key_0]
        for idx_1, key_1 in enumerate(sig_ann_keys[idx_0+1:]):
            ann_1 = signal_anns[key_1]
            for r_symb in ANN_SYMBS:
                r_idxs = np.array([idx for (idx, symb) in zip(ann_0.sample, ann_0.symbol) if symb == r_symb])
                r_idxs1 = np.array([idx for (idx, symb) in zip(ann_1.sample, ann_1.symbol) if symb == r_symb])
                try:
                    c = processing.compare_annotations(r_idxs, r_idxs1, int(0.02 * r.fs))
                    sig_ann_tp_count[key_0] += c.tp
                    sig_ann_tp_count[key_1] += c.tp
                except:
                    pass
    lead_candidates = []
    for sig_idx, ann in signal_anns.items():
        symb_counter = Counter(ann.symbol)
        candidate = True
        for v in ANN_SYMBS:
            if symb_counter.get(v, 0) < 2:
                candidate = False
                print("not a candidate ", v)
                break
        if candidate:
           lead_candidates.append(sig_idx)

    # print(lead_candidates)
    fallback_lead = max(lead_candidates, key=(lambda k: sig_ann_tp_count[k]))

    # Step 3: Calculate all statistical measurements of the lead, for each lead
    for idx, lead in enumerate(LEADS):
        #ann = signal_anns.get(idx, signal_anns[fallback_lead])        
        if idx not in lead_candidates:
            ann = signal_anns.get(fallback_lead)
        else:
            ann = signal_anns.get(idx)
        idx_2_symb = list(zip(ann.sample, ann.symbol))
        
        #print(lead_candidates)
        #print(idx)
        #print(idx_2_symb)

        # Get R-peak indicies
        r_idxs = list((idx) for (idx, symb) in idx_2_symb if symb == "N")
        # Get R-peak amplitude statistics
        r_amps = list(r.p_signal[:, sig_idx][idx] for idx in r_idxs)
        features[f"{lead}_R-peak"] = _get_stats(r_amps)

        # Get P-wave peak indicies
        p_idxs = list((idx) for (idx, symb) in idx_2_symb if symb == "p")
        # Get P-wave peak ampitude statistics
        p_amps = list(r.p_signal[:, sig_idx][idx] for idx in p_idxs)
        features[f"{lead}_P-peak"] = _get_stats(p_amps)

        # Get T-wave peak indicies
        t_idxs = list((idx) for (idx, symb) in idx_2_symb if symb == "t")
        # Get T-wave peak amplitude statistics
        t_amps = list(r.p_signal[:, sig_idx][idx] for idx in t_idxs)
        features[f"{lead}_T-peak"] = _get_stats(t_amps)

        # Get heart rate as normal beats per minute (distance between R-peaks)
        hr = list(r.fs / interval * 60 for interval in np.diff(r_idxs))
        # Get heart rate statistics
        features[f"{lead}_HR"] = _get_stats(hr)
        
        # Calculate the P wave, QRS duration, T wave duration,
        # PR segment, ST segment, PR interval, ST interval
        p_wave_dur = []   # (, p, )
        qrs_dur = []      # (, r, )
        t_wave_dur = []   # (, t, )
        pr_segment = []   # p, ), (, N # distance between ) and (
        st_segment = []   # N, ), (, t # distance between ) and (
        pr_interval = []  # (, p, ), (, N # distance between ( and (
        st_interval = []  # N, ), (, t, ) # distance between ) and )

        # state machine variables
        # assumes all waveforms are enclosed and not-overlapping
        last_waveform = None
        in_waveform = None
        segment_start = 0
        segment_end = 0
        last_waveform_end = 0
        last_waveform_start = 0
        waveform_start = 0

        for idx_symb in idx_2_symb:
            idx, symb = idx_symb
            if symb == "(":
                # a waveform has started, but we don't know what it is yet. record index
                last_waveform_start = waveform_start
                waveform_start = idx
            elif symb == ")":
                # update the durations
                waveform_duration = (idx - waveform_start) / r.fs
                if in_waveform == "p":
                    p_wave_dur.append(waveform_duration)
                elif in_waveform == "N":
                    qrs_dur.append(waveform_duration)
                elif in_waveform == "t":
                    t_wave_dur.append(waveform_duration)
                
                # check the st_interval
                if last_waveform == "N" and in_waveform == "t":
                    st_interval.append((segment_end - last_waveform_end) / r.fs)

                # we are no longer in a waveform, as it has closed.
                last_waveform = in_waveform
                in_waveform = None
                last_waveform_end = segment_end
                segment_end = idx
            elif symb == "p":
                # we are in waveform 'p'
                segment_start = idx
                in_waveform = "p"
            elif symb == "N":
                # we are in waveform 'QRS'
                if last_waveform == "p":
                    pr_segment.append((segment_end - segment_start) / r.fs)
                    pr_interval.append((waveform_start - last_waveform_start) / r.fs)

                in_waveform = "N"
                segment_start = idx
            elif symb == "t":
                if last_waveform == "N":
                    st_segment.append((segment_end - segment_start) / r.fs)
                # we are in waveform 't'
                in_waveform = "t"
        
        features[f"{lead}_P-wave_duration"] = _get_stats(p_wave_dur)
        features[f"{lead}_QRS_duration"] = _get_stats(qrs_dur)
        features[f"{lead}_T-wave_duration"] = _get_stats(t_wave_dur)   # (, t, )
        features[f"{lead}_PR_segment"] = _get_stats(pr_segment)   # p, ), (, N # distance between ) and (
        features[f"{lead}_ST_segment"] = _get_stats(st_segment)   # N, ), (, t # distance between ) and (
        features[f"{lead}_PR_interval"] = _get_stats(pr_interval)  # (, p, ), (, N # distance between ( and (
        features[f"{lead}_ST_interval"] = _get_stats(st_interval)  # N, ), (, t, ) # distance between ) and )

        # features["annotations"] = signal_anns
    
    return features


In [ ]:
def worker_fn(rn):
    try:
        return extract_features(rn, ann_dir="experiments/PhysioNet2020/feat_extraction/out")
    except Exception as e:
        raise e
        return {"error": e, "err_fn": rn}

# out = worker_fn(record_names[71])
out = worker_fn(record_names[718])

print(out.keys())
if out.get("error"):
    print(out["error"])

Writing file A0719.mat with 24 empty leading bytes
Writing file A0719.mat with 24 empty leading bytes
Writing file A0719.mat with 24 empty leading bytes
Writing file A0719.mat with 24 empty leading bytes
Writing file A0719.mat with 24 empty leading bytes


In [6]:
# worker_fn = partial(extract_features, ann_dir="experiments/PhysioNet2020/feat_extraction/out")
with tqdm(record_names) as t:
    with Pool(initializer=tqdm.set_lock, initargs=(tqdm.get_lock(),)) as p:
       out = list(p.imap_unordered(worker_fn, t))
#     out = list([worker_fn(rn) for rn in t])

  0%|          | 1/6877 [00:00<11:44,  9.75it/s]

Writing file A0012.mat with 24 empty leading bytes
Writing file A0002.mat with 24 empty leading bytes
Writing file A0007.mat with 24 empty leading bytes
Writing file A0019.mat with 24 empty leading bytes
Writing file A0010.mat with 24 empty leading bytes
Writing file A0001.mat with 24 empty leading bytes
Writing file A0005.mat with 24 empty leading bytes
Writing file A0024.mat with 24 empty leading bytes
Writing file A0009.mat with 24 empty leading bytes
Writing file A0008.mat with 24 empty leading bytes
Writing file A0018.mat with 24 empty leading bytes
Writing file A0016.mat with 24 empty leading bytes
Writing file A0020.mat with 24 empty leading bytes
Writing file A0015.mat with 24 empty leading bytes
Writing file A0013.mat with 24 empty leading bytes
Writing file A0014.mat with 24 empty leading bytes
Writing file A0021.mat with 24 empty leading bytes
Writing file A0006.mat with 24 empty leading bytes
Writing file A0017.mat with 24 empty leading bytes
Writing file A0023.mat with 24 

 14%|█▎        | 935/6877 [00:24<07:52, 12.57it/s]

Writing file A0056.mat with 24 empty leading bytes
Writing file A0055.mat with 24 empty leading bytes
Writing file A0057.mat with 24 empty leading bytes
Writing file A0059.mat with 24 empty leading bytes
Writing file A0058.mat with 24 empty leading bytes
Writing file A0060.mat with 24 empty leading bytes
Writing file A0062.mat with 24 empty leading bytes
Writing file A0061.mat with 24 empty leading bytes
Writing file A0064.mat with 24 empty leading bytes
Writing file A0063.mat with 24 empty leading bytes
Writing file A0065.mat with 24 empty leading bytes
Writing file A0066.mat with 24 empty leading bytes
Writing file A0067.mat with 24 empty leading bytes
Writing file A0049.mat with 24 empty leading bytes
Writing file A0056.mat with 24 empty leading bytes
Writing file A0068.mat with 24 empty leading bytes
Writing file A0050.mat with 24 empty leading bytes
Writing file A0051.mat with 24 empty leading bytes
Writing file A0070.mat with 24 empty leading bytes
Writing file A0069.mat with 24 

 14%|█▎        | 935/6877 [00:40<07:52, 12.57it/s]

...

 99%|█████████▉| 6793/6877 [47:15<00:40,  2.06it/s]

Writing file A5909.mat with 24 empty leading bytes
Writing file A5920.mat with 24 empty leading bytes
Writing file A5905.mat with 24 empty leading bytes
Writing file A5904.mat with 24 empty leading bytes
Writing file A5901.mat with 24 empty leading bytes
Writing file A5900.mat with 24 empty leading bytes
Writing file A5912.mat with 24 empty leading bytes
Writing file A5910.mat with 24 empty leading bytes
Writing file A5915.mat with 24 empty leading bytes
Writing file A5902.mat with 24 empty leading bytes
Writing file A5917.mat with 24 empty leading bytes
Writing file A5906.mat with 24 empty leading bytes
Writing file A5916.mat with 24 empty leading bytes
Writing file A5922.mat with 24 empty leading bytes
Writing file A5918.mat with 24 empty leading bytes
Writing file A5908.mat with 24 empty leading bytes
Writing file A5923.mat with 24 empty leading bytes
Writing file A5913.mat with 24 empty leading bytes
Writing file A5903.mat with 24 empty leading bytes
Writing file A5907.mat with 24 

100%|██████████| 6877/6877 [47:42<00:00,  2.40it/s]

Writing file A5964.mat with 24 empty leading bytes
Writing file A5969.mat with 24 empty leading bytes
Writing file A5971.mat with 24 empty leading bytes
Writing file A5961.mat with 24 empty leading bytes
Writing file A5967.mat with 24 empty leading bytes
Writing file A5965.mat with 24 empty leading bytes
Writing file A5972.mat with 24 empty leading bytes


Writing file A5979.mat with 24 empty leading bytes
Writing file A5966.mat with 24 empty leading bytes
Writing file A5974.mat with 24 empty leading bytes
Writing file A5977.mat with 24 empty leading bytes
Writing file A5980.mat with 24 empty leading bytes
Writing file A5973.mat with 24 empty leading bytes
Writing file A5960.mat with 24 empty leading bytes
Writing file A5975.mat with 24 empty leading bytes
Writing file A5959.mat with 24 empty leading bytes
Writing file A5962.mat with 24 empty leading bytes
Writing file A5970.mat with 24 empty leading bytes
Writing file A5968.mat with 24 empty leading bytes
Writing file A5976.mat with 24 empty leading bytes
Writing file A5981.mat with 24 empty leading bytes
Writing file A5967.mat with 24 empty leading bytes
Writing file A5978.mat with 24 empty leading bytes
Writing file A5958.mat with 24 empty leading bytes
Writing file A5963.mat with 24 empty leading bytes
Writing file A5971.mat with 24 empty leading bytes
Writing file A5961.mat with 24 

In [7]:
err_fns = []
for features in out:
    err_fn = features.get("err_fn", None)
    if err_fn:
        err_fns.append(err_fn)

In [13]:
# print(err_fns)
# print(len(err_fns))
out[10]


{'error': ValueError('max() arg is an empty sequence'),
 'err_fn': 'Training_WFDB/A0017'}